In [50]:
# Importing the required libraries
import credentials as cd


from fyers_apiv3 import fyersModel


import pandas as pd


import datetime as dt

In [51]:
# Reading the access token from the file
with open("access.txt", "r") as a:


    access_token = a.read()


client_id = cd.client_id



# Initialize the FyersModel instance with your client_id, access_token, and enable async mode


fyers = fyersModel.FyersModel(
    client_id=client_id, is_async=False, token=access_token, log_path=""
)

In [52]:
# Fetching the historical data for Nifty 50 index for 5 minutes interval for the month of May 2024 using the history API endpoint of Fyers API
data = {
    "symbol": "NSE:NIFTY50-INDEX",
    "resolution": "5",
    "date_format": "1",
    "range_from": "2024-03-02",
    "range_to": "2024-05-30",
    "cont_flag": "1",
}


response = fyers.history(data=data)
# print(response)
data = response["candles"]
df = pd.DataFrame(data)
print(df)

               0         1         2         3         4  5
0     1709351100  22406.95  22420.25  22381.30  22381.30  0
1     1709351400  22381.70  22381.70  22366.95  22375.55  0
2     1709351700  22375.90  22387.55  22371.65  22385.30  0
3     1709352000  22386.40  22399.30  22385.50  22397.35  0
4     1709352300  22396.80  22408.35  22395.15  22397.20  0
...          ...       ...       ...       ...       ... ..
3766  1716024900  22506.80  22506.80  22506.80  22506.80  0
3767  1716025200  22506.80  22506.80  22506.80  22506.80  0
3768  1716025500  22506.80  22506.80  22506.80  22506.80  0
3769  1716025800  22506.80  22506.80  22506.80  22506.80  0
3770  1716026100  22506.80  22506.80  22506.80  22506.80  0

[3771 rows x 6 columns]


In [53]:
# Converting the UNIX timestamp to datetime format and setting the date column as the index of the dataframe and saving the data to a CSV file
df.columns = ["date", "open", "high", "low", "close", "volume"]


df["date"] = pd.to_datetime(df["date"], unit="s")



df.date = df.date.dt.tz_localize("UTC").dt.tz_convert("Asia/Kolkata")
print(df)



df["date"] = df["date"].dt.tz_localize(None)


df = df.set_index("date")

print(df)
df.to_csv("data.csv")



print(dt.datetime.now())

                          date      open      high       low     close  volume
0    2024-03-02 09:15:00+05:30  22406.95  22420.25  22381.30  22381.30       0
1    2024-03-02 09:20:00+05:30  22381.70  22381.70  22366.95  22375.55       0
2    2024-03-02 09:25:00+05:30  22375.90  22387.55  22371.65  22385.30       0
3    2024-03-02 09:30:00+05:30  22386.40  22399.30  22385.50  22397.35       0
4    2024-03-02 09:35:00+05:30  22396.80  22408.35  22395.15  22397.20       0
...                        ...       ...       ...       ...       ...     ...
3766 2024-05-18 15:05:00+05:30  22506.80  22506.80  22506.80  22506.80       0
3767 2024-05-18 15:10:00+05:30  22506.80  22506.80  22506.80  22506.80       0
3768 2024-05-18 15:15:00+05:30  22506.80  22506.80  22506.80  22506.80       0
3769 2024-05-18 15:20:00+05:30  22506.80  22506.80  22506.80  22506.80       0
3770 2024-05-18 15:25:00+05:30  22506.80  22506.80  22506.80  22506.80       0

[3771 rows x 6 columns]
                         op

In [54]:
import mplfinance as mpf

# Plotting the candlestick chart
mpf.plot(df, type="candle", volume=True)

c:\Users\Shiva Kumar G\AppData\Local\Programs\Python\Python312\Lib\site-packages\mplfinance\_arg_validators.py:84: UserWarning: 


            POSSIBLE TO SEE DETAILS (Candles, Ohlc-Bars, Etc.)
   For more information see:
   - https://github.com/matplotlib/mplfinance/wiki/Plotting-Too-Much-Data
   
   TO SILENCE THIS WARNING, set `type='line'` in `mpf.plot()`
   OR set kwarg `warn_too_much_data=N` where N is an integer 
   LARGER than the number of data points you want to plot.

  warnings.warn('\n\n ================================================================= '+


<IPython.core.display.Javascript object>

c:\Users\Shiva Kumar G\AppData\Local\Programs\Python\Python312\Lib\site-packages\mplfinance\plotting.py:707: UserWarning: Attempting to set identical low and high ylims makes transformation singular; automatically expanding.
  volumeAxes.set_ylim(vymin,vymax)


In [55]:
import numpy as np

# Strategy to identify the bullish and bearish candlestick patterns using MACD and RSI indicators
# Strategy to buy and sell based on the EMA crossover, fast EMA = 9, slow EMA = 13

df["macd"] = (
    df["close"].ewm(span=9, adjust=False).mean()
    - df["close"].ewm(span=13, adjust=False).mean()
)

df["signal"] = df["macd"].ewm(span=5, adjust=False).mean()

df["rsi"] = 100 - (
    100
    / (
        1
        + (df["close"].diff(1).clip(lower=0) / df["close"].diff(1).clip(upper=0))
        .rolling(window=14)
        .mean()
    )
)

df["buy_signal"] = np.where((df["macd"] > df["signal"]) & (df["rsi"] > 50), 1, 0)

df["sell_signal"] = np.where((df["macd"] < df["signal"]) & (df["rsi"] < 50), 1, 0)


df["fast_ema"] = df["close"].ewm(span=9, adjust=False).mean()
df["slow_ema"] = df["close"].ewm(span=13, adjust=False).mean()

df.tail()

open     high      low    close  volume      macd  \
date                                                                        
2024-05-18 15:05:00  22506.8  22506.8  22506.8  22506.8       0  0.065713   
2024-05-18 15:10:00  22506.8  22506.8  22506.8  22506.8       0  0.056668   
2024-05-18 15:15:00  22506.8  22506.8  22506.8  22506.8       0  0.048846   
2024-05-18 15:20:00  22506.8  22506.8  22506.8  22506.8       0  0.042087   
2024-05-18 15:25:00  22506.8  22506.8  22506.8  22506.8       0  0.036250   

                       signal  rsi  buy_signal  sell_signal      fast_ema  \
date                                                                        
2024-05-18 15:05:00  0.095577  NaN           0            0  22506.794006   
2024-05-18 15:10:00  0.082607  NaN           0            0  22506.795205   
2024-05-18 15:15:00  0.071354  NaN           0            0  22506.796164   
2024-05-18 15:20:00  0.061598  NaN           0            0  22506.796931   
2024-05-18 15:25:00  0.053149  NaN           0            0  22506.797545   

                         slow_ema  
date                               
2024-05-18 15:05:00  22506.728294  
2024-05-18 15:10:00  22506.738538  
2024-05-18 15:15:00  22506.747318  
2024-05-18 15:20:00  22506.754844  
2024-05-18 15:25:00  22506.761295

In [56]:
# draw plot

import matplotlib.pyplot as plt

plt.plot(df["close"], label="Close Price", color="black")
plt.plot(df["fast_ema"], label="Fast EMA", color="red")
plt.plot(df["slow_ema"], label="Slow EMA", color="blue")
plt.show()

<IPython.core.display.Javascript object>

In [57]:
# define entries

df["Long"] = df.fast_ema > df.slow_ema
df.tail()

open     high      low    close  volume      macd  \
date                                                                        
2024-05-18 15:05:00  22506.8  22506.8  22506.8  22506.8       0  0.065713   
2024-05-18 15:10:00  22506.8  22506.8  22506.8  22506.8       0  0.056668   
2024-05-18 15:15:00  22506.8  22506.8  22506.8  22506.8       0  0.048846   
2024-05-18 15:20:00  22506.8  22506.8  22506.8  22506.8       0  0.042087   
2024-05-18 15:25:00  22506.8  22506.8  22506.8  22506.8       0  0.036250   

                       signal  rsi  buy_signal  sell_signal      fast_ema  \
date                                                                        
2024-05-18 15:05:00  0.095577  NaN           0            0  22506.794006   
2024-05-18 15:10:00  0.082607  NaN           0            0  22506.795205   
2024-05-18 15:15:00  0.071354  NaN           0            0  22506.796164   
2024-05-18 15:20:00  0.061598  NaN           0            0  22506.796931   
2024-05-18 15:25:00  0.053149  NaN           0            0  22506.797545   

                         slow_ema  Long  
date                                     
2024-05-18 15:05:00  22506.728294  True  
2024-05-18 15:10:00  22506.738538  True  
2024-05-18 15:15:00  22506.747318  True  
2024-05-18 15:20:00  22506.754844  True  
2024-05-18 15:25:00  22506.761295  True

Step-by-Step Trading Strategy
1. Setup Indicators
    a. MACD (Moving Average Convergence Divergence):
        * MACD Line: 9-period EMA minus 13-period EMA.
        * Signal Line: 9-period EMA of the MACD Line.
        * Histogram: MACD Line minus Signal Line.
    b. Exponential Moving Averages (EMAs):
        9-period EMA.
        13-period EMA.
Relative Strength Index (RSI):
14-period RSI.
2. Identify the Trend Using MACD
Bullish Trend:
When the MACD Line crosses above the Signal Line.
Bearish Trend:
When the MACD Line crosses below the Signal Line.
3. Secondary Confirmation with EMA Crossover
Bullish Confirmation:
The 9 EMA crosses above the 13 EMA.
Bearish Confirmation:
The 9 EMA crosses below the 13 EMA.
4. Use RSI for Entry and Exit Signals
Entry Signal (Bullish):
RSI is above 30 and trending upwards (indicating increasing momentum).
Exit Signal (Bullish):
RSI is above 70 (indicating overbought conditions, potential reversal).
Entry Signal (Bearish):
RSI is below 70 and trending downwards (indicating decreasing momentum).
Exit Signal (Bearish):
RSI is below 30 (indicating oversold conditions, potential reversal).
Trading Strategy Rules
Long Position (Buying)
MACD Signal:
Wait for the MACD Line to cross above the Signal Line.
EMA Confirmation:
Wait for the 9 EMA to cross above the 13 EMA.
RSI Check:
Ensure RSI is above 30 and trending upwards.
Entry:
Enter a long position when all the above conditions are met.
Exit:
Exit the position when RSI reaches above 70 or when the 9 EMA crosses below the 13 EMA.
Short Position (Selling)
MACD Signal:
Wait for the MACD Line to cross below the Signal Line.
EMA Confirmation:
Wait for the 9 EMA to cross below the 13 EMA.
RSI Check:
Ensure RSI is below 70 and trending downwards.
Entry:
Enter a short position when all the above conditions are met.
Exit:
Exit the position when RSI drops below 30 or when the 9 EMA crosses above the 13 EMA.
Example Workflow
Entering a Long Trade:
MACD Crossover:
MACD Line crosses above the Signal Line on the daily chart.
EMA Confirmation:
A few days later, the 9 EMA crosses above the 13 EMA.
RSI Check:
RSI is at 40 and moving upwards.
Enter Trade:
Enter a long position.
Monitoring:
Monitor the RSI and EMAs regularly.
Exit Trade:
Exit the position when RSI reaches 70 or when 9 EMA crosses below 13 EMA.
Entering a Short Trade:
MACD Crossover:
MACD Line crosses below the Signal Line on the daily chart.
EMA Confirmation:
A few days later, the 9 EMA crosses below the 13 EMA.
RSI Check:
RSI is at 60 and moving downwards.
Enter Trade:
Enter a short position.
Monitoring:
Monitor the RSI and EMAs regularly.
Exit Trade:
Exit the position when RSI drops to 30 or when 9 EMA crosses above 13 EMA.

In [58]:
# pip install pandas numpy ta matplotlib

In [59]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import ta


def compute_indicators(data):
    # Compute the 9 and 13 period EMAs
    data["9_EMA"] = ta.trend.ema_indicator(data["close"], window=9)
    data["13_EMA"] = ta.trend.ema_indicator(data["close"], window=13)

    # Compute the MACD using 9 and 13 period EMAs
    data["MACD_Line"] = ta.trend.ema_indicator(
        data["close"], window=9
    ) - ta.trend.ema_indicator(data["close"], window=13)
    data["Signal_Line"] = ta.trend.ema_indicator(data["MACD_Line"], window=9)
    data["MACD_Hist"] = data["MACD_Line"] - data["Signal_Line"]

    # Compute the RSI
    data["RSI"] = ta.momentum.rsi(data["close"], window=14)

    return data


def generate_signals(data):
    data["Signal"] = 0
    data["Position"] = 0

    for i in range(1, len(data)):
        # Long position entry conditions
        if (
            data["MACD_Line"].iloc[i] > data["Signal_Line"].iloc[i]
            and data["9_EMA"].iloc[i] > data["13_EMA"].iloc[i]
            and data["RSI"].iloc[i] > 30
        ):
            data["Signal"].iloc[i] = 1
        # Long position exit conditions
        elif (
            data["RSI"].iloc[i] >= 70 or data["9_EMA"].iloc[i] < data["13_EMA"].iloc[i]
        ):
            data["Signal"].iloc[i] = -1
        # Short position entry conditions
        elif (
            data["MACD_Line"].iloc[i] < data["Signal_Line"].iloc[i]
            and data["9_EMA"].iloc[i] < data["13_EMA"].iloc[i]
            and data["RSI"].iloc[i] < 70
        ):
            data["Signal"].iloc[i] = -1
        # Short position exit conditions
        elif (
            data["RSI"].iloc[i] <= 30 or data["9_EMA"].iloc[i] > data["13_EMA"].iloc[i]
        ):
            data["Signal"].iloc[i] = 1

    data["Position"] = data["Signal"].replace(to_replace=0, method="ffill")

    return data


def plot_data(data):
    plt.figure(figsize=(14, 10))

    # Plot close price and EMAs
    plt.subplot(3, 1, 1)
    plt.plot(data["close"], label="close Price", color="blue")
    plt.plot(data["9_EMA"], label="9 EMA", color="orange")
    plt.plot(data["13_EMA"], label="13 EMA", color="green")
    plt.legend()
    plt.title("close Price and EMAs")

    # Plot MACD
    plt.subplot(3, 1, 2)
    plt.plot(data["MACD_Line"], label="MACD Line", color="blue")
    plt.plot(data["Signal_Line"], label="Signal Line", color="orange")
    plt.bar(data.index, data["MACD_Hist"], label="MACD Histogram", color="green")
    plt.legend()
    plt.title("MACD")

    # Plot RSI
    plt.subplot(3, 1, 3)
    plt.plot(data["RSI"], label="RSI", color="blue")
    plt.axhline(70, color="red", linestyle="--")
    plt.axhline(30, color="green", linestyle="--")
    plt.legend()
    plt.title("RSI")

    plt.tight_layout()
    plt.show()


def main():
    # Load data (example uses Yahoo Finance CSV format)
    # data = pd.read_csv("path_to_your_data.csv", parse_dates=True, index_col="Date")
    data = df

    # Compute indicators
    data = compute_indicators(data)

    # Generate signals
    data = generate_signals(data)

    # Plot data and signals
    plot_data(data)


if __name__ == "__main__":
    main()

C:\Users\Shiva Kumar G\AppData\Local\Temp\ipykernel_15056\1788305780.py:53: FutureWarning: ChainedAssignmentError: behaviour will change in pandas 3.0!
You are setting values through chained assignment. Currently this works in certain cases, but when using Copy-on-Write (which will become the default behaviour in pandas 3.0) this will never work to update the original DataFrame or Series, because the intermediate object on which we are setting values will behave as a copy.
A typical example is when you are setting values in a column of a DataFrame, like:

df["col"][row_indexer] = value

Use `df.loc[row_indexer, "col"] = values` instead, to perform the assignment in a single step and ensure this keeps updating the original `df`.

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

  data["Signal"].iloc[i] = 1
C:\Users\Shiva Kumar G\AppData\Local\Temp\ipykernel_15056\1788305780.py:53: SettingWithCopyW

<IPython.core.display.Javascript object>

In [60]:
import os
import pandas as pd
import backtrader as bt
import ta


class MACDEMA_RSI_Strategy(bt.Strategy):
    params = (
        ("macd1", 9),
        ("macd2", 13),
        ("macdsig", 9),
        ("ema1", 9),
        ("ema2", 13),
        ("rsi_period", 14),
    )

    def __init__(self):
        # Compute MACD
        macd = bt.ind.MACD(
            self.data.close,
            period_me1=self.params.macd1,
            period_me2=self.params.macd2,
            period_signal=self.params.macdsig,
        )
        self.macd_line = macd.macd
        self.signal_line = macd.signal

        # Compute EMAs
        self.ema1 = bt.ind.EMA(self.data.close, period=self.params.ema1)
        self.ema2 = bt.ind.EMA(self.data.close, period=self.params.ema2)

        # Compute RSI
        self.rsi = bt.ind.RSI(self.data.close, period=self.params.rsi_period)

        self.order = None  # To keep track of pending orders

        # To store signals
        self.signals = []

    def next(self):
        if self.order:
            return  # If an order is pending, do nothing

        signal = None
        if self.position:
            # Check for exit signal
            if (self.rsi > 90) or (self.ema1 < self.ema2):
                self.order = self.sell()
                signal = "Sell"
            elif (self.rsi < 20) or (self.ema1 > self.ema2):
                self.order = self.buy()
                signal = "Buy"
        else:
            # Check for entry signal
            if (
                (self.macd_line > self.signal_line)
                and (self.ema1 > self.ema2)
                # and (self.rsi > 52)
            ):
                self.order = self.buy()
                signal = "Buy"
            elif (
                (self.macd_line < self.signal_line)
                and (self.ema1 < self.ema2)
                # and (self.rsi < 48)
            ):
                self.order = self.sell()
                signal = "Sell"

        if signal:
            self.signals.append(
                {
                    "date": self.data.datetime.date(0),
                    "signal": signal,
                    "close": self.data.close[0],
                    "macd_line": self.macd_line[0],
                    "signal_line": self.signal_line[0],
                    "ema1": self.ema1[0],
                    "ema2": self.ema2[0],
                    "rsi": self.rsi[0],
                }
            )

    def stop(self):
        # Export signals to CSV
        df = pd.DataFrame(self.signals)
        # Check if the file exists
        if os.path.exists("signals.csv"):
            # If the file exists, append without writing the header
            df.to_csv("signals.csv", mode="a", header=False, index=False)
        else:
            # If the file does not exist, write the header
            df.to_csv("signals.csv", index=False)

        print("Signals exported to signals.csv")


def main():
    # Load data
    # data = pd.read_csv("path_to_your_data.csv", parse_dates=True, index_col="Date")
    data = df
    # Prepare the data for Backtrader
    data_bt = bt.feeds.PandasData(dataname=data)

    # Initialize Cerebro engine
    cerebro = bt.Cerebro()

    # Add strategy
    cerebro.addstrategy(MACDEMA_RSI_Strategy)

    # Add data feed
    cerebro.adddata(data_bt)

    # Set our desired cash start
    cerebro.broker.set_cash(100000)

    # Set the commission
    cerebro.broker.setcommission(commission=0.001)

    # Print out the starting conditions
    print("Starting Portfolio Value: %.2f" % cerebro.broker.getvalue())

    # Run the backtest
    cerebro.run()

    # Print out the final result
    print("Final Portfolio Value: %.2f" % cerebro.broker.getvalue())

    # Plot the result
    cerebro.plot()


if __name__ == "__main__":
    main()

Starting Portfolio Value: 100000.00
Signals exported to signals.csv
Final Portfolio Value: 99874.30


<IPython.core.display.Javascript object>

In [61]:
# # due to API restriction, data can't fetched for more than 60 days at a time, so we need to fetch data in chunks of 60 days and then concatenate them to get the complete data
# def fetchOHLC(ticker, interval, duration):
#     """extracts historical data and outputs in the form of dataframe"""
#     instrument = ticker
#     data = {
#         "symbol": instrument,
#         "resolution": interval,
#         "date_format": "1",
#         "range_from": dt.date.today() - dt.timedelta(duration),
#         "range_to": dt.date.today(),
#         "cont_flag": "1",
#     }
#     sdata = fyers.history(data)
#     sdata = pd.DataFrame(sdata["candles"])
#     sdata.columns = ["date", "open", "high", "low", "close", "volume"]
#     sdata["date"] = pd.to_datetime(sdata["date"], unit="s")
#     sdata.date = sdata.date.dt.tz_localize("UTC").dt.tz_convert("Asia/Kolkata")
#     sdata["date"] = sdata["date"].dt.tz_localize(None)
#     sdata = sdata.set_index("date")
#     return sdata


# ticker = "NSE:NIFTYBANK-INDEX"
# data = fetchOHLC(ticker, "D", 60)
# print(data)


# def gethistory(symbol1, type, duration):
#     symbol = "NSE:" + symbol1 + "-" + type
#     start = dt.date.today() - dt.timedelta(duration)
#     end = dt.date.today() - dt.timedelta()
#     sdata = pd.DataFrame()
#     while start <= end:
#         end2 = start + dt.timedelta(60)
#         data = {
#             "symbol": symbol,
#             "resolution": "1",
#             "date_format": "1",
#             "range_from": start,
#             "range_to": end2,
#             "cont_flag": "1",
#         }
#         s = fyers.history(data)
#         s = pd.DataFrame(s["candles"])
#         sdata = pd.concat([sdata, s], ignore_index=True)
#         start = end2 + dt.timedelta(1)
#     sdata.columns = ["date", "open", "high", "low", "close", "volume"]
#     sdata["date"] = pd.to_datetime(sdata["date"], unit="s")
#     sdata.date = sdata.date.dt.tz_localize("UTC").dt.tz_convert("Asia/Kolkata")
#     sdata["date"] = sdata["date"].dt.tz_localize(None)
#     sdata = sdata.set_index("date")
#     return sdata


# data = gethistory("NIFTYBANK", "INDEX", 3000)
# print(data)
# data.to_csv("niftybank.csv")